# Instructions

1. Place your desired song in the same directory as this notebook. *This notebook was designed for .wav files! Other formats may not work*
2. Put the name of your song in "filename", with the .wav extension at the end.
3. Put the desired title of your visualization under videoname, with the .mp4 extension at the end.
4. Run all blocks.
5. Tune if necessary under the "Mandelbrot params, testing utils" block

Misc. notes: 
Demo song "fall_sumn_v5.wav" is provided.

Block size should be a power of 2 to fully leverage FFT; 2048 is recommended (yields ~20 FPS, smaller block sizes will yield more FPS but takes longer to generate and may be too responsive, leading to lots of flickering)

*Warning: 
Do not touch "fractal_viz.mp4" and "mono_data.m4a". The mp4 file is the visualization generated before attaching the audio. The m4a file is the song converted to mono for FFT. (Corollary: music with extreme stereo information/lots of phase cancellation, especially in the <150hz region, may not work properly with this visualizer)*

In [ ]:
### PUT FILE NAMES HERE ###
filename = "fall_sumn_v5.wav"
videoname = "animation5.mp4"

In [ ]:
import matplotlib.pyplot as plt
%config InlineBackend.figure_format = 'retina'
from scipy.fft import fft, fftfreq
from scipy.signal.windows import blackman, hamming
import numpy as np
import simpleaudio as sa
from scipy.io import wavfile
import colorednoise as cn
import moviepy.editor as mpe
from moviepy.video.io import ffmpeg_tools

def PrintArrayInfo(a,name=''):
    if (len(name)==0):
        print("Array info:")
    else:
        print("Array:", name)
    print("shape:", a.shape)
    print("dtype:", a.dtype)
    print("min, max:", a.min(), a.max())
    print()

In [ ]:
def Play(rate,data):
    # Start playback
    play_obj = sa.play_buffer(data, 1, 2, rate)
    # Wait for playback to finish before exiting
    play_obj.wait_done()

# Preprocessing

### Reading files - put files here!

In [ ]:
from scipy.signal.windows import blackman, hamming
from matplotlib.animation import FFMpegWriter
mono_data_path = "mono_data.m4a"

# rate, data = wavfile.read("Promenade_very_short_mono.wav")
rate, data = wavfile.read(filename)
data = np.mean(data, axis=1)
print(data)

# optional cropping
# start_seconds = 40
# end_seconds = 45

# start_sample = rate * start_seconds
# end_sample = rate * end_seconds

# data = data[start_sample:end_sample]

wavfile.write(mono_data_path, rate, data.astype(np.int16))
# check it isn't broken ((VOLUME WARNING!!!))
# Play(rate, data.astype(np.int16))

### FFT parameters

Suggestion:
- Lows = <150hz: 150 / rate
- Mids = 150-6000: 6000 / rate
- Highs: 6000+: 6000 / rate

In [ ]:
# FFT junk ------

# Block size; default = 2048
N = 2048

# sample spacing
# affects maximum frequency!
# T = 1.0 / 800.0
T = 1.0 / rate
x = np.linspace(0.0, N*T, N, endpoint=False)

# div rate by 2 because nyquist
# lows = 0
# mids = int(N * (150 / (rate/2)))
# highs = int(N * (6000 / (rate/2)))

# default: 0
lows_cutoff = 0
# default: 150
mids_cutoff = 200
# default: 6000
highs_cutoff = 6000

# print(x)
# block = 150
# # generate sample function
# # y = np.sin(2000.0 * 2.0*np.pi*x) + 0.5*np.sin(12000.0 * 2.0*np.pi*x)

num_blocks = len(data) // N

### Mandelbrot params, testing utils

In [ ]:
plot_dim = 201
step_size = 2.5/plot_dim
# arange is [inc,inc] apparently
xp = np.arange(-2,0.5, (2.5)/plot_dim)
yp = np.arange(-1.25, 1.25, (2.5)/plot_dim)

A_2 = np.zeros((plot_dim,plot_dim))

# parameters
n_max = 50
z_limit = 50

# base mandelbrot func
def mandelbrot(z, C):
    zNew = z**2 + C
    return zNew

def determine_diverge_init(C, init, iterations):
#     z = complex(0,0)
    z = init
    for n in range(iterations):
        # Value blows up really fast
        # so cap it so it doesn't kill itself
        z = mandelbrot(z, C)
        if abs(z) > z_limit:
            return n
    
    return iterations

# note: strongest when init is at (0,0)
# probably have some constant default value, then depending on value of freq shave off some to get it closer to 0?

# breaks with any n_max < 4
# best range seems to be 4 - 200
# n_max = 50

### OPTIMAL SETTINGS FOR BASS CONTROLLING FRACTAL
# thresholds for fft
max_lows = 1e5
min_lows = 8e3
# max_mids = 4e2
max_mids = 2e2
# min_mids = 1e2
min_mids = 1e1
max_highs = 1e3
min_highs = 1e2

# bounds to pass into mandelbrot; brightest at min_iter
base_iter = 100
# max, min_iter subtracted from base_iter, so real range is
# 10 - 100
max_iter = 90
min_iter = 0
max_real = 1.5
min_real = 0
max_im = 0
min_im = -0.2

### OPTIMAL SETTINGS FOR MIDS CONTROLLING FRACTAL
# # thresholds for fft
# max_lows = 1.2e4
# min_lows = 8e3
# max_mids = 2.5e3
# min_mids = 5e2
# max_highs = 2e2
# min_highs = 1e2

# # bounds to pass into mandelbrot; brightest at min_iter
# base_iter = 100
# # max, min_iter subtracted from base_iter, so real range is
# # 10 - 100
# max_iter = 90
# min_iter = 0
# max_real = 1.5
# min_real = 0
# max_im = 1.5
# min_im = 0


# normalization
# https://stats.stackexchange.com/questions/178626/how-to-normalize-data-between-1-and-1 
# https://stackoverflow.com/questions/42562111/how-to-skew-normalization-using-a-logarithmic-scale

# goes by log
def normalize(enteredValue, minEntry, maxEntry, normalizedMin, normalizedMax):
#     print("entered:", enteredValue)
#     print("max:", maxEntry)
    enteredValue = max(min(enteredValue, maxEntry-1), minEntry+1)
#     print("entered:", enteredValue)
    # i don't really get how this line works honestly
    mx = (np.emath.logn(10, enteredValue-minEntry)/(np.emath.logn(10, maxEntry-minEntry)));
#     print("mx:", mx)
    preshiftNormalized = mx*(normalizedMax-normalizedMin);
#     print(preshiftNormalized)
    shiftedNormalized = preshiftNormalized + normalizedMin;

    return shiftedNormalized;

def lin_normalize(enteredValue, minEntry, maxEntry, normalizedMin, normalizedMax):
#     print("entered:", enteredValue)
#     print("max:", maxEntry)
    enteredValue = max(min(enteredValue, maxEntry), minEntry)
#     print("entered:", enteredValue)
    # i don't really get how this line works honestly
    mx = (enteredValue-minEntry)/(maxEntry-minEntry);
#     print("mx:", mx)
    preshiftNormalized = mx*(normalizedMax-normalizedMin);
#     print(preshiftNormalized)
    shiftedNormalized = preshiftNormalized + normalizedMin;

    return shiftedNormalized;

Debug mandelbrot set

In [ ]:
for i in range(plot_dim):
    for j in range(plot_dim):
        A_2[i,j] = determine_diverge_init(complex(xp[i],yp[j]), complex(1.5,0), 10)

plt.imshow(A_2)
plt.show()

# Generate video

In [ ]:
metadata = dict(title='FFT spectrum visualizer, mandelbrot', artist='anjo',comment='oh yeah babey')
writer = FFMpegWriter(fps=(rate / N), metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

ymin = 1e-2
ymax = 1e6

peak_lows_data = []
real_lows_data = []

peak_mids_data = []
real_mids_data = []

peak_highs_data = []
real_highs_data = []

with writer.saving(fig, "fractal_viz.mp4", dpi=200):

    for block in range(num_blocks):
        y = data[N*block:N*(block+1)]

#         yf = fft(y)
#         print(yf.shape)
        w = hamming(N)
        ywf = fft(y*w)
        xf = fftfreq(N, T)[:N//2]
        
        ywf_real = 2.0/N * np.abs(ywf[1:N//2])
        
        len_ywf = ywf_real.shape[0]
        lows = 0
        mids = int(len_ywf * (mids_cutoff / (rate/2)))
        # alternate option: start mid-band at 1.5k
        # 808 might have interfering harmonics?
        mids_start = int(len_ywf * (1500 / (rate/2)))
        highs = int(len_ywf * (highs_cutoff / (rate/2)))
        
        max_real_lows = max(ywf_real[:mids])
        max_real_mids = np.mean(ywf_real[mids:highs])
        max_real_highs = max(ywf_real[highs:])
        
#         print(max_real_lows, max_real_mids, max_real_highs)
        
        ## MIDS CONTROLS FRACTAL SHAPE
#         print("normalizing lows:")
#         peak_lows = int(base_iter - normalize(max_real_lows, min_lows, max_lows, min_iter, max_iter))
#         print("normalizing mids:")
#         peak_mids = max_real - lin_normalize(max_real_mids, min_mids, max_mids, min_real, max_real)
#         print("normalizing highs:")
#         peak_highs = max_im - lin_normalize(max_real_highs, min_highs, max_highs, min_im, max_im)
        
        ## BASS CONTROLS FRACTAL SHAPE
#         print("normalizing mids:")
        peak_mids = int(base_iter - lin_normalize(max_real_mids, min_mids, max_mids, min_iter, max_iter))
#         print("normalizing lows:")
        peak_lows = max_real - normalize(max_real_lows, min_lows, max_lows, min_real, max_real)
#         print("normalizing highs:")
        peak_highs = max_im - lin_normalize(max_real_highs, min_highs, max_highs, min_im, max_im)
        
        ## BASS SHAPE, HIGHS BLOOM
# #         print("normalizing mids:")
#         peak_highs = int(base_iter - lin_normalize(max_real_highs, min_highs, max_highs, min_iter, max_iter))
# #         print("normalizing lows:")
#         peak_lows = max_real - normalize(max_real_lows, min_lows, max_lows, min_real, max_real)
# #         print("normalizing highs:")
#         peak_mids = max_im - lin_normalize(max_real_mids, min_mids, max_mids, min_im, max_im)
        
        peak_lows_data.append(peak_lows)
        real_lows_data.append(max_real_lows)
        
        peak_mids_data.append(peak_mids)
        real_mids_data.append(max_real_mids)
        
        peak_highs_data.append(peak_highs)
        real_highs_data.append(max_real_highs)
        
#         print(type(peak_lows), type(peak_mids), type(peak_highs))
        
        # haaaiilll mary
        for i in range(plot_dim):
            for j in range(plot_dim):
                A_2[i,j] = determine_diverge_init(complex(xp[i],yp[j]), complex(peak_lows, 0), peak_mids)
        
        fig.clear()
        ax = fig.add_subplot(111)
        ax.imshow(A_2)
#         plt.imshow(A_2)
        
        if block % 100 == 0:
            print("block:", block)
            print("result:", peak_lows, peak_mids)
            ax.imshow(A_2)
            plt.imshow(A_2)
            plt.draw()
            plt.show()
#         plt.draw()
        plt.pause(1 / rate)
        writer.grab_frame()
        
# my_clip = mpe.VideoFileClip('fractal_viz.mp4')
# audio_background = mpe.AudioFileClip(filename)
# final_clip = my_clip.set_audio(audio_background)
# final_clip.write_videofile("fractal_viz_sound.mp4", audio=True, audio_codec='aac', temp_audiofile='temp-audio.m4a', remove_temp=True)
# ffmpeg_tools.ffmpeg_merge_video_audio("fractal_viz.mp4", "fall_sumn_v5_cropped.wav", 'fractal_viz_sound.mp4')

### Attach audio

In [ ]:
my_clip = mpe.VideoFileClip('fractal_viz.mp4')
audio_background = mpe.AudioFileClip(filename)
final_clip = my_clip.set_audio(audio_background)
final_clip.write_videofile(videoname, fps=30, audio=True, audio_codec='aac', temp_audiofile='temp-audio.m4a', remove_temp=True)
# ffmpeg_tools.ffmpeg_merge_video_audio("fractal_viz.mp4", "fall_sumn_v5_cropped.wav", 'fractal_viz_sound.mp4')

# Input data visualization - may be useful for tuning

In [ ]:
plt.plot(peak_lows_data, label="peak_lows")
plt.show()
plt.plot(real_lows_data, color='orange', label="real_lows")
plt.show()

In [ ]:
plt.plot(peak_mids_data, label="peak_mids")
plt.show()
plt.plot(real_mids_data, color='orange', label="real_mids")
plt.show()

In [ ]:
plt.plot(peak_highs_data, label="peak_highs")
plt.show()
plt.plot(real_highs_data, color='orange', label="real_highs")
plt.show()